In [156]:
import os
import bs4 as bs
import requests
import pandas as pd
from recsys.imdb_parser import metadata, reviews
from recsys.imdb_parser import identifiers
from recsys import utils

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [17]:
response = requests.get('https://www.imdb.com/title/tt0468569/', headers={"Accept-Language": "en-US,en;q=0.5"})
soup = bs.BeautifulSoup(response.text, 'lxml')

In [90]:
CREDENTIALS_PATH = os.path.join('..', 'scripts', 'config', 'credentials.yaml')

aws_credentials = utils.parse_config(CREDENTIALS_PATH, 'aws')
access_key = aws_credentials['access_key']
secret_access_key = aws_credentials['secret_access_key']

In [5]:
df = pd.DataFrame(data={'a': [1, 2, 3], 'b': [1, 4, 6]})
df

a  b
0  1  1
1  2  4
2  3  6

In [4]:
os.listdir('../tests/data')

['page_with_identifiers.pkl', 'review_tag_example.pkl']

In [5]:
import pickle

with open('../tests/data/page_with_identifiers.pkl', 'rb') as f:
    page = pickle.load(f)

In [16]:
url = 'https://www.imdb.com/title/tt7991608/'
resp = requests.get(url)
soup = bs.BeautifulSoup(resp.content, 'lxml')

In [56]:
utils.save_df(df, 'test.csv', metadata_config, aws_credentials)

SaveResponse(is_successful=True, exception_msg='')

In [39]:
soup.find('li', {'data-testid': 'title-techspec_runtime'}).div.text

'2 hours 32 minutes'

In [29]:
CONFIG_FILE = os.path.join('..', 'scripts', 'config', 'parser_config.yaml')
metadata_config = utils.parse_config(CONFIG_FILE, 'metadata')
metadata_config

{'metadata_file': 'data/metadata/metadata.json',
 'genres': 'all',
 'min_delay': 0.1,
 'max_delay': 0.2,
 'log_file': 'logs/imdb_parser/details.log',
 'log_level': 'INFO',
 'log_msg_format': '%(asctime)s %(levelname)s %(message)s',
 'log_dt_format': '%Y-%m-%d %H:%M:%S'}

In [157]:
reviews_config = utils.parse_config(CONFIG_FILE, 'reviews')
reviews_config

{'bucket': 'movie-on-friday',
 'metadata_file': 'metadata/metadata.json',
 'review_folder': 'reviews',
 'n_reviews': None,
 'pct_reviews': 100,
 'sleep_time': 0.2,
 'log_file': 'logs/imdb_parser/reviews.log',
 'log_level': 'INFO',
 'log_msg_format': '%(asctime)s %(levelname)s %(message)s',
 'log_dt_format': '%Y-%m-%d %H:%M:%S'}

In [162]:
revcol = reviews.ReviewCollector(reviews_config, aws_credentials)

In [175]:
os.path.join('s3://', 'movie-on-friday', 'reviews', 'tt0468569', '.csv')

's3://movie-on-friday/reviews/tt0468569/.csv'

In [163]:
darkknight_reviews = revcol.collect_title_reviews('/title/tt0468569/')

25
50
75
100
125
150
175
200
225
250
275
300
325
350
375
400
425
450
475
500
525
550
575
600
625
650
675
699
724
749
774
799
823
848
873
898
923
948
973
998
1023
1048
1073
1098
1123
1148
1173
1198
1223
1248
1273
1298
1323
1348
1373
1398
1423
1448
1473
1498
1523
1548
1573
1597
1622
1647
1672
1697
1722
1747
1772
1797
1822
1847
1872
1897
1922
1947
1972
1997
2022
2047
2072
2097
2122
2147
2172
2197
2222
2247
2272
2297
2322
2347
2372
2397
2422
2447
2472
2497
2522
2547
2572
2597
2622
2647
2672
2697
2722
2747
2772
2797
2822
2847
2872
2897
2922
2947
2972
2997
3022
3047
3072
3097
3122
3147
3172
3197
3222
3247
3272
3297
3322
3347
3372
3397
3422
3447
3472
3497
3522
3547
3571
3596
3621
3646
3671
3696
3721
3746
3771
3796
3821
3846
3871
3896
3921
3946
3971
3996
4021
4046
4071
4096
4121
4146
4171
4196
4221
4246
4271
4296
4321
4346
4371
4396
4421
4446
4471
4496
4521
4546
4571
4596
4621
4646
4671
4696
4721
4745
4770
4795
4820
4845
4870
4895
4920
4945
4970
4995
5020
5045
5070
5095
5120
5145
5170
5195
522

In [167]:
pd.DataFrame.from_records(darkknight_reviews).memory_usage(deep=True).sum() / 1024 / 1024

14.016203880310059

In [169]:
500 * 23000 / 25

460000.0

In [5]:
movie_metadata = utils.read_json(os.path.join('..', metadata_config['metadata_file']))
genres = {item['main_genre'] for item in movie_metadata.values()}
genres

{'Action',
 'Adventure',
 'Animation',
 'Biography',
 'Comedy',
 'Crime',
 'Drama',
 'Family',
 'Fantasy',
 'Film-Noir',
 'Horror',
 'Mystery',
 'Romance',
 'Sci-Fi',
 'Western'}

In [9]:
utils.wait(0, 1)

In [6]:
movie_metadata

{'/title/tt0468569/': {'main_genre': 'Action',
  'original_title': 'The Dark Knight',
  'genres': ['Action', 'Crime', 'Drama'],
  'review_summary': {'user_review_num': '8.1K',
   'critic_review_num': '435',
   'metascore': '84'},
  'agg_rating': {'avg_rating': '9.0/10', 'num_votes': '2.6M'},
  'actors': {'Christian Bale': '/name/nm0000288?ref_=tt_cl_t_1',
   'Heath Ledger': '/name/nm0005132?ref_=tt_cl_t_2',
   'Aaron Eckhart': '/name/nm0001173?ref_=tt_cl_t_3',
   'Michael Caine': '/name/nm0000323?ref_=tt_cl_t_4',
   'Maggie Gyllenhaal': '/name/nm0350454?ref_=tt_cl_t_5',
   'Gary Oldman': '/name/nm0000198?ref_=tt_cl_t_6',
   'Morgan Freeman': '/name/nm0000151?ref_=tt_cl_t_7',
   'Monique Gabriela Curnen': '/name/nm1010931?ref_=tt_cl_t_8',
   'Ron Dean': '/name/nm0212939?ref_=tt_cl_t_9',
   'Cillian Murphy': '/name/nm0614165?ref_=tt_cl_t_10'},
  'imdb_recommendations': ['/title/tt1345836/?ref_=tt_sims_tt_t_1',
   '/title/tt0372784/?ref_=tt_sims_tt_t_2',
   '/title/tt1375666/?ref_=tt_sims

In [30]:
detcol = metadata.MetadataCollector(metadata_config)

In [35]:
s = '/name/nm0425005?ref_=tt_cl_t_1'
s.split('?')[0]

'/name/nm0425005'

In [38]:
int(s.split('tt_cl_t_')[1])

1

In [61]:
red_notice_metadata = detcol.collect_title_details(soup)
red_notice_metadata

{'original_title': 'Red Notice',
 'genres': ['Action', 'Comedy', 'Thriller'],
 'poster_url': 'https://m.media-amazon.com/images/M/MV5BZmRjODgyMzEtMzIxYS00OWY2LTk4YjUtMGMzZjMzMTZiN2Q0XkEyXkFqcGdeQXVyMTkxNjUyNQ@@._V1_QL75_UX190_CR0,0,190,281_.jpg',
 'review_summary': {'user_review_num': '1.8K',
  'critic_review_num': '196',
  'metascore': '37'},
 'agg_rating': {'avg_rating': '6.3/10', 'num_votes': '262K'},
 'actors': {'1': '/name/nm0425005',
  '2': '/name/nm0005351',
  '3': '/name/nm2933757',
  '4': '/name/nm5709125',
  '5': '/name/nm0224565',
  '6': '/name/nm3543262',
  '7': '/name/nm0024188',
  '8': '/name/nm0676152',
  '9': '/name/nm0584492',
  '10': '/name/nm6011424'},
 'imdb_recommendations': {'1': '/title/tt2463208/',
  '2': '/title/tt6264654/',
  '3': '/title/tt8106534/',
  '4': '/title/tt8706598/',
  '5': '/title/tt8672748/',
  '6': '/title/tt1959563/',
  '7': '/title/tt8385148/',
  '8': '/title/tt19064676/',
  '9': '/title/tt17017830/',
  '10': '/title/tt11286314/',
  '11': '/ti

In [62]:
utils.write_json(red_notice_metadata, 'here.json')

In [81]:
metadata = utils.read_json('../data/metadata/metadata.json')
print(len(metadata))

23583


In [149]:
os.path.join('s3://', 'movie-on-friday', 'metadata/metadata.json')

's3://movie-on-friday/metadata/metadata.json'

In [ ]:
            options = {
                'key': credentials['access_key'],
                'secret': credentials['secret_access_key']
            }

In [186]:
metadata = pd.read_json(
    's3://movie-on-friday/metadata/metadata.json', orient='index',
    storage_options={'key': access_key, 'secret': secret_access_key}
)
metadata.head()

main_genre              original_title  \
/title/tt0002130/  Adventure             Dante's Inferno   
/title/tt0003740/  Adventure                     Cabiria   
/title/tt0004635/     Action               The Squaw Man   
/title/tt0004707/     Comedy  Tillie's Punctured Romance   
/title/tt0004972/      Drama       The Birth of a Nation   

                                        genres  \
/title/tt0002130/  [Adventure, Drama, Fantasy]   
/title/tt0003740/  [Adventure, Drama, History]   
/title/tt0004635/     [Action, Drama, Romance]   
/title/tt0004707/                     [Comedy]   
/title/tt0004972/        [Drama, History, War]   

                                                          poster_url  \
/title/tt0002130/  https://m.media-amazon.com/images/M/MV5BNjU1ND...   
/title/tt0003740/  https://m.media-amazon.com/images/M/MV5BZmVjNz...   
/title/tt0004635/  https://m.media-amazon.com/images/M/MV5BMjMwOD...   
/title/tt0004707/  https://m.media-amazon.com/images/M/MV5BMDZjOW...   
/title/tt0004972/  https://m.media-amazon.com/images/M/MV5BNWZlNj...   

                                                      review_summary  \
/title/tt0002130/  {'user_review_num': '36', 'critic_review_num':...   
/title/tt0003740/  {'user_review_num': '35', 'critic_review_num':...   
/title/tt0004635/  {'user_review_num': '9', 'critic_review_num': ...   
/title/tt0004707/  {'user_review_num': '41', 'critic_review_num':...   
/title/tt0004972/  {'user_review_num': '379', 'critic_review_num'...   

                                                      agg_rating  \
/title/tt0002130/  {'avg_rating': '7.0/10', 'num_votes': '2.9K'}   
/title/tt0003740/  {'avg_rating': '7.1/10', 'num_votes': '3.6K'}   
/title/tt0004635/   {'avg_rating': '5.7/10', 'num_votes': '979'}   
/title/tt0004707/  {'avg_rating': '6.3/10', 'num_votes': '3.5K'}   
/title/tt0004972/   {'avg_rating': '6.2/10', 'num_votes': '25K'}   

                                                              actors  \
/title/tt0002130/  {'1': '/name/nm0660139', '2': '/name/nm0685283...   
/title/tt0003740/  {'1': '/name/nm0021935', '2': '/name/nm0702894...   
/title/tt0004635/  {'1': '/name/nm0267914', '2': '/name/nm0758457...   
/title/tt0004707/  {'1': '/name/nm0000122', '2': '/name/nm0237597...   
/title/tt0004972/  {'1': '/name/nm0001273', '2': '/name/nm0550615...   

                                                imdb_recommendations  \
/title/tt0002130/  {'1': '/title/tt0003740/', '2': '/title/tt0001...   
/title/tt0003740/  {'1': '/title/tt0006864/', '2': '/title/tt0009...   
/title/tt0004635/  {'1': '/title/tt0014532/', '2': '/title/tt0006...   
/title/tt0004707/  {'1': '/title/tt0005074/', '2': '/title/tt0006...   
/title/tt0004972/  {'1': '/title/tt0006864/', '2': '/title/tt0009...   

                                                             details  \
/title/tt0002130/  {'release_date': ['July 1911 (United States)']...   
/title/tt0003740/  {'release_date': ['May 9, 1914 (United States)...   
/title/tt0004635/  {'release_date': ['February 15, 1914 (United S...   
/title/tt0004707/  {'release_date': ['December 21, 1914 (United S...   
/title/tt0004972/  {'release_date': ['March 21, 1915 (United Stat...   

                                                           boxoffice  
/title/tt0002130/  {'budget': None, 'boxoffice_gross_domestic': N...  
/title/tt0003740/  {'budget': 'ITL 1,000,000 (estimated)', 'boxof...  
/title/tt0004635/  {'budget': '$20,000 (estimated)', 'boxoffice_g...  
/title/tt0004707/  {'budget': '$50,000 (estimated)', 'boxoffice_g...  
/title/tt0004972/  {'budget': '$110,000 (estimated)', 'boxoffice_...

In [187]:
metadata['reviews_collected_flg'] = 0
metadata[['reviews_collected_flg']].to_json(
    's3://movie-on-friday/reviews/status.json',
    storage_options={'key': access_key, 'secret': secret_access_key}
)

In [208]:
status = pd.read_json(
    's3://movie-on-friday/metadata/metadata.json',
    storage_options={'key': access_key, 'secret': secret_access_key},
    orient='index'
)
status.head()

main_genre              original_title  \
/title/tt0002130/  Adventure             Dante's Inferno   
/title/tt0003740/  Adventure                     Cabiria   
/title/tt0004635/     Action               The Squaw Man   
/title/tt0004707/     Comedy  Tillie's Punctured Romance   
/title/tt0004972/      Drama       The Birth of a Nation   

                                        genres  \
/title/tt0002130/  [Adventure, Drama, Fantasy]   
/title/tt0003740/  [Adventure, Drama, History]   
/title/tt0004635/     [Action, Drama, Romance]   
/title/tt0004707/                     [Comedy]   
/title/tt0004972/        [Drama, History, War]   

                                                          poster_url  \
/title/tt0002130/  https://m.media-amazon.com/images/M/MV5BNjU1ND...   
/title/tt0003740/  https://m.media-amazon.com/images/M/MV5BZmVjNz...   
/title/tt0004635/  https://m.media-amazon.com/images/M/MV5BMjMwOD...   
/title/tt0004707/  https://m.media-amazon.com/images/M/MV5BMDZjOW...   
/title/tt0004972/  https://m.media-amazon.com/images/M/MV5BNWZlNj...   

                                                      review_summary  \
/title/tt0002130/  {'user_review_num': '36', 'critic_review_num':...   
/title/tt0003740/  {'user_review_num': '35', 'critic_review_num':...   
/title/tt0004635/  {'user_review_num': '9', 'critic_review_num': ...   
/title/tt0004707/  {'user_review_num': '41', 'critic_review_num':...   
/title/tt0004972/  {'user_review_num': '379', 'critic_review_num'...   

                                                      agg_rating  \
/title/tt0002130/  {'avg_rating': '7.0/10', 'num_votes': '2.9K'}   
/title/tt0003740/  {'avg_rating': '7.1/10', 'num_votes': '3.6K'}   
/title/tt0004635/   {'avg_rating': '5.7/10', 'num_votes': '979'}   
/title/tt0004707/  {'avg_rating': '6.3/10', 'num_votes': '3.5K'}   
/title/tt0004972/   {'avg_rating': '6.2/10', 'num_votes': '25K'}   

                                                              actors  \
/title/tt0002130/  {'1': '/name/nm0660139', '2': '/name/nm0685283...   
/title/tt0003740/  {'1': '/name/nm0021935', '2': '/name/nm0702894...   
/title/tt0004635/  {'1': '/name/nm0267914', '2': '/name/nm0758457...   
/title/tt0004707/  {'1': '/name/nm0000122', '2': '/name/nm0237597...   
/title/tt0004972/  {'1': '/name/nm0001273', '2': '/name/nm0550615...   

                                                imdb_recommendations  \
/title/tt0002130/  {'1': '/title/tt0003740/', '2': '/title/tt0001...   
/title/tt0003740/  {'1': '/title/tt0006864/', '2': '/title/tt0009...   
/title/tt0004635/  {'1': '/title/tt0014532/', '2': '/title/tt0006...   
/title/tt0004707/  {'1': '/title/tt0005074/', '2': '/title/tt0006...   
/title/tt0004972/  {'1': '/title/tt0006864/', '2': '/title/tt0009...   

                                                             details  \
/title/tt0002130/  {'release_date': ['July 1911 (United States)']...   
/title/tt0003740/  {'release_date': ['May 9, 1914 (United States)...   
/title/tt0004635/  {'release_date': ['February 15, 1914 (United S...   
/title/tt0004707/  {'release_date': ['December 21, 1914 (United S...   
/title/tt0004972/  {'release_date': ['March 21, 1915 (United Stat...   

                                                           boxoffice  
/title/tt0002130/  {'budget': None, 'boxoffice_gross_domestic': N...  
/title/tt0003740/  {'budget': 'ITL 1,000,000 (estimated)', 'boxof...  
/title/tt0004635/  {'budget': '$20,000 (estimated)', 'boxoffice_g...  
/title/tt0004707/  {'budget': '$50,000 (estimated)', 'boxoffice_g...  
/title/tt0004972/  {'budget': '$110,000 (estimated)', 'boxoffice_...

In [214]:
pd.DataFrame(status).to_json('here.json')

In [220]:
js = pd.read_json('here.json', orient='index')
js.head()

main_genre              original_title  \
/title/tt0002130/  Adventure             Dante's Inferno   
/title/tt0003740/  Adventure                     Cabiria   
/title/tt0004635/     Action               The Squaw Man   
/title/tt0004707/     Comedy  Tillie's Punctured Romance   
/title/tt0004972/      Drama       The Birth of a Nation   

                                        genres  \
/title/tt0002130/  [Adventure, Drama, Fantasy]   
/title/tt0003740/  [Adventure, Drama, History]   
/title/tt0004635/     [Action, Drama, Romance]   
/title/tt0004707/                     [Comedy]   
/title/tt0004972/        [Drama, History, War]   

                                                          poster_url  \
/title/tt0002130/  https://m.media-amazon.com/images/M/MV5BNjU1ND...   
/title/tt0003740/  https://m.media-amazon.com/images/M/MV5BZmVjNz...   
/title/tt0004635/  https://m.media-amazon.com/images/M/MV5BMjMwOD...   
/title/tt0004707/  https://m.media-amazon.com/images/M/MV5BMDZjOW...   
/title/tt0004972/  https://m.media-amazon.com/images/M/MV5BNWZlNj...   

                                                      review_summary  \
/title/tt0002130/  {'user_review_num': '36', 'critic_review_num':...   
/title/tt0003740/  {'user_review_num': '35', 'critic_review_num':...   
/title/tt0004635/  {'user_review_num': '9', 'critic_review_num': ...   
/title/tt0004707/  {'user_review_num': '41', 'critic_review_num':...   
/title/tt0004972/  {'user_review_num': '379', 'critic_review_num'...   

                                                      agg_rating  \
/title/tt0002130/  {'avg_rating': '7.0/10', 'num_votes': '2.9K'}   
/title/tt0003740/  {'avg_rating': '7.1/10', 'num_votes': '3.6K'}   
/title/tt0004635/   {'avg_rating': '5.7/10', 'num_votes': '979'}   
/title/tt0004707/  {'avg_rating': '6.3/10', 'num_votes': '3.5K'}   
/title/tt0004972/   {'avg_rating': '6.2/10', 'num_votes': '25K'}   

                                                              actors  \
/title/tt0002130/  {'1': '/name/nm0660139', '2': '/name/nm0685283...   
/title/tt0003740/  {'1': '/name/nm0021935', '2': '/name/nm0702894...   
/title/tt0004635/  {'1': '/name/nm0267914', '2': '/name/nm0758457...   
/title/tt0004707/  {'1': '/name/nm0000122', '2': '/name/nm0237597...   
/title/tt0004972/  {'1': '/name/nm0001273', '2': '/name/nm0550615...   

                                                imdb_recommendations  \
/title/tt0002130/  {'1': '/title/tt0003740/', '2': '/title/tt0001...   
/title/tt0003740/  {'1': '/title/tt0006864/', '2': '/title/tt0009...   
/title/tt0004635/  {'1': '/title/tt0014532/', '2': '/title/tt0006...   
/title/tt0004707/  {'1': '/title/tt0005074/', '2': '/title/tt0006...   
/title/tt0004972/  {'1': '/title/tt0006864/', '2': '/title/tt0009...   

                                                             details  \
/title/tt0002130/  {'release_date': ['July 1911 (United States)']...   
/title/tt0003740/  {'release_date': ['May 9, 1914 (United States)...   
/title/tt0004635/  {'release_date': ['February 15, 1914 (United S...   
/title/tt0004707/  {'release_date': ['December 21, 1914 (United S...   
/title/tt0004972/  {'release_date': ['March 21, 1915 (United Stat...   

                                                           boxoffice  
/title/tt0002130/  {'budget': None, 'boxoffice_gross_domestic': N...  
/title/tt0003740/  {'budget': 'ITL 1,000,000 (estimated)', 'boxof...  
/title/tt0004635/  {'budget': '$20,000 (estimated)', 'boxoffice_g...  
/title/tt0004707/  {'budget': '$50,000 (estimated)', 'boxoffice_g...  
/title/tt0004972/  {'budget': '$110,000 (estimated)', 'boxoffice_...

In [223]:
js.to_json('here2.json', orient='index')

In [226]:
from tqdm import tqdm

li = range(1000000)
s = 0
for i, k in tqdm(enumerate(li), total=len(li)):
    s += k**2

100%|██████████| 1000000/1000000 [00:00<00:00, 1995565.73it/s]


In [227]:
i

999999

In [224]:
pd.read_json('here2.json', orient='index')

main_genre              original_title  \
/title/tt0002130/  Adventure             Dante's Inferno   
/title/tt0003740/  Adventure                     Cabiria   
/title/tt0004635/     Action               The Squaw Man   
/title/tt0004707/     Comedy  Tillie's Punctured Romance   
/title/tt0004972/      Drama       The Birth of a Nation   
...                      ...                         ...   
/title/tt9898858/     Action                        None   
/title/tt9900782/     Action                        None   
/title/tt9907782/    Fantasy                        None   
/title/tt9911196/     Comedy                        None   
/title/tt9916362/      Drama                        None   

                                        genres  \
/title/tt0002130/  [Adventure, Drama, Fantasy]   
/title/tt0003740/  [Adventure, Drama, History]   
/title/tt0004635/     [Action, Drama, Romance]   
/title/tt0004707/                     [Comedy]   
/title/tt0004972/        [Drama, History, War]   
...                                        ...   
/title/tt9898858/                         None   
/title/tt9900782/                         None   
/title/tt9907782/                         None   
/title/tt9911196/                         None   
/title/tt9916362/                         None   

                                                          poster_url  \
/title/tt0002130/  https://m.media-amazon.com/images/M/MV5BNjU1ND...   
/title/tt0003740/  https://m.media-amazon.com/images/M/MV5BZmVjNz...   
/title/tt0004635/  https://m.media-amazon.com/images/M/MV5BMjMwOD...   
/title/tt0004707/  https://m.media-amazon.com/images/M/MV5BMDZjOW...   
/title/tt0004972/  https://m.media-amazon.com/images/M/MV5BNWZlNj...   
...                                                              ...   
/title/tt9898858/                                               None   
/title/tt9900782/                                               None   
/title/tt9907782/                                               None   
/title/tt9911196/                                               None   
/title/tt9916362/                                               None   

                                                      review_summary  \
/title/tt0002130/  {'user_review_num': '36', 'critic_review_num':...   
/title/tt0003740/  {'user_review_num': '35', 'critic_review_num':...   
/title/tt0004635/  {'user_review_num': '9', 'critic_review_num': ...   
/title/tt0004707/  {'user_review_num': '41', 'critic_review_num':...   
/title/tt0004972/  {'user_review_num': '379', 'critic_review_num'...   
...                                                              ...   
/title/tt9898858/                                               None   
/title/tt9900782/                                               None   
/title/tt9907782/                                               None   
/title/tt9911196/                                               None   
/title/tt9916362/                                               None   

                                                      agg_rating  \
/title/tt0002130/  {'avg_rating': '7.0/10', 'num_votes': '2.9K'}   
/title/tt0003740/  {'avg_rating': '7.1/10', 'num_votes': '3.6K'}   
/title/tt0004635/   {'avg_rating': '5.7/10', 'num_votes': '979'}   
/title/tt0004707/  {'avg_rating': '6.3/10', 'num_votes': '3.5K'}   
/title/tt0004972/   {'avg_rating': '6.2/10', 'num_votes': '25K'}   
...                                                          ...   
/title/tt9898858/                                           None   
/title/tt9900782/                                           None   
/title/tt9907782/                                           None   
/title/tt9911196/                                           None   
/title/tt9916362/                                           None   

                                                              actors  \
/title/tt0002130/  {'1': '/name/nm0660139', '2': '/name/nm0685283...   
/titl

In [200]:
pd.DataFrame(status.T.to_dict()).to_json('here.json', orient='index')

In [207]:
s3.Bucket('movie-on-friday')

AttributeError: 'S3' object has no attribute 'Bucket'

In [206]:
s3.list_objects_v2(Bucket='movie-on-friday', Prefix='metadata/')

{'ResponseMetadata': {'RequestId': 'KG60DWSG9KMVZEKC',
  'HostId': 'EA78AGeStSW/vF95lh628RJCYTWVUNJaRFg9m0yjev+c2NNRfhUlSgEMk1WONrxS6ykyIua40Ws=',
  'HTTPStatusCode': 200,
  'HTTPHeaders': {'x-amz-id-2': 'EA78AGeStSW/vF95lh628RJCYTWVUNJaRFg9m0yjev+c2NNRfhUlSgEMk1WONrxS6ykyIua40Ws=',
   'x-amz-request-id': 'KG60DWSG9KMVZEKC',
   'date': 'Thu, 14 Jul 2022 09:43:10 GMT',
   'x-amz-bucket-region': 'us-east-1',
   'content-type': 'application/xml',
   'transfer-encoding': 'chunked',
   'server': 'AmazonS3'},
  'RetryAttempts': 0},
 'IsTruncated': False,
 'Contents': [{'Key': 'metadata/',
   'LastModified': datetime.datetime(2022, 5, 30, 8, 14, 49, tzinfo=tzutc()),
   'ETag': '"d41d8cd98f00b204e9800998ecf8427e"',
   'Size': 0,
   'StorageClass': 'STANDARD'},
  {'Key': 'metadata/metadata.json',
   'LastModified': datetime.datetime(2022, 7, 14, 1, 20, 35, tzinfo=tzutc()),
   'ETag': '"bbe2808c98d7d1f797524b0761cb2508-6"',
   'Size': 35356388,
   'StorageClass': 'STANDARD'}],
 'Name': 'movie-on

In [201]:
pd.read_json('here.json', orient='column')

reviews_collected_flg
/title/tt0002130/                      0
/title/tt0003740/                      0
/title/tt0004635/                      0
/title/tt0004707/                      0
/title/tt0004972/                      0
...                                  ...
/title/tt9898858/                      0
/title/tt9900782/                      0
/title/tt9907782/                      0
/title/tt9911196/                      0
/title/tt9916362/                      0

[23584 rows x 1 columns]

In [181]:
pd.DataFrame(st.T.to_dict()).to_json(
    's3://movie-on-friday/reviews/status.json',
    orient=''
    storage_options={'key': access_key, 'secret': secret_access_key}
)

In [150]:
pandas_json = pd.read_json('s3://movie-on-friday/metadata/metadata.json', orient='index',
             storage_options={'key': access_key, 'secret': secret_access_key})
pandas_json

main_genre              original_title  \
/title/tt0002130/  Adventure             Dante's Inferno   
/title/tt0003740/  Adventure                     Cabiria   
/title/tt0004635/     Action               The Squaw Man   
/title/tt0004707/     Comedy  Tillie's Punctured Romance   
/title/tt0004972/      Drama       The Birth of a Nation   
...                      ...                         ...   
/title/tt9898858/     Action                        None   
/title/tt9900782/     Action                        None   
/title/tt9907782/    Fantasy                        None   
/title/tt9911196/     Comedy                        None   
/title/tt9916362/      Drama                        None   

                                        genres  \
/title/tt0002130/  [Adventure, Drama, Fantasy]   
/title/tt0003740/  [Adventure, Drama, History]   
/title/tt0004635/     [Action, Drama, Romance]   
/title/tt0004707/                     [Comedy]   
/title/tt0004972/        [Drama, History, War]   
...                                        ...   
/title/tt9898858/                         None   
/title/tt9900782/                         None   
/title/tt9907782/                         None   
/title/tt9911196/                         None   
/title/tt9916362/                         None   

                                                          poster_url  \
/title/tt0002130/  https://m.media-amazon.com/images/M/MV5BNjU1ND...   
/title/tt0003740/  https://m.media-amazon.com/images/M/MV5BZmVjNz...   
/title/tt0004635/  https://m.media-amazon.com/images/M/MV5BMjMwOD...   
/title/tt0004707/  https://m.media-amazon.com/images/M/MV5BMDZjOW...   
/title/tt0004972/  https://m.media-amazon.com/images/M/MV5BNWZlNj...   
...                                                              ...   
/title/tt9898858/                                               None   
/title/tt9900782/                                               None   
/title/tt9907782/                                               None   
/title/tt9911196/                                               None   
/title/tt9916362/                                               None   

                                                      review_summary  \
/title/tt0002130/  {'user_review_num': '36', 'critic_review_num':...   
/title/tt0003740/  {'user_review_num': '35', 'critic_review_num':...   
/title/tt0004635/  {'user_review_num': '9', 'critic_review_num': ...   
/title/tt0004707/  {'user_review_num': '41', 'critic_review_num':...   
/title/tt0004972/  {'user_review_num': '379', 'critic_review_num'...   
...                                                              ...   
/title/tt9898858/                                               None   
/title/tt9900782/                                               None   
/title/tt9907782/                                               None   
/title/tt9911196/                                               None   
/title/tt9916362/                                               None   

                                                      agg_rating  \
/title/tt0002130/  {'avg_rating': '7.0/10', 'num_votes': '2.9K'}   
/title/tt0003740/  {'avg_rating': '7.1/10', 'num_votes': '3.6K'}   
/title/tt0004635/   {'avg_rating': '5.7/10', 'num_votes': '979'}   
/title/tt0004707/  {'avg_rating': '6.3/10', 'num_votes': '3.5K'}   
/title/tt0004972/   {'avg_rating': '6.2/10', 'num_votes': '25K'}   
...                                                          ...   
/title/tt9898858/                                           None   
/title/tt9900782/                                           None   
/title/tt9907782/                                           None   
/title/tt9911196/                                           None   
/title/tt9916362/                                           None   

                                                              actors  \
/title/tt0002130/  {'1': '/name/nm0660139', '2': '/name/nm0685283...   
/titl

In [153]:
pandas_json[['main_genre']].T.to_dict()

{'/title/tt0002130/': {'main_genre': 'Adventure'},
 '/title/tt0003740/': {'main_genre': 'Adventure'},
 '/title/tt0004635/': {'main_genre': 'Action'},
 '/title/tt0004707/': {'main_genre': 'Comedy'},
 '/title/tt0004972/': {'main_genre': 'Drama'},
 '/title/tt0006206/': {'main_genre': 'Action'},
 '/title/tt0006780/': {'main_genre': 'Romance'},
 '/title/tt0006864/': {'main_genre': 'Drama'},
 '/title/tt0009893/': {'main_genre': 'Comedy'},
 '/title/tt0009900/': {'main_genre': 'Adventure'},
 '/title/tt0009968/': {'main_genre': 'Drama'},
 '/title/tt0010323/': {'main_genre': 'Horror'},
 '/title/tt0010600/': {'main_genre': 'Comedy'},
 '/title/tt0010726/': {'main_genre': 'Adventure'},
 '/title/tt0010806/': {'main_genre': 'Comedy'},
 '/title/tt0011130/': {'main_genre': 'Drama'},
 '/title/tt0011237/': {'main_genre': 'Fantasy'},
 '/title/tt0011439/': {'main_genre': 'Adventure'},
 '/title/tt0011565/': {'main_genre': 'Crime'},
 '/title/tt0011841/': {'main_genre': 'Drama'},
 '/title/tt0011870/': {'main_

In [98]:
len([v for v in pandas_json.to_dict().values() if 'original_title' in v])

23583

In [101]:
for k, v in pandas_json.items():
    print(v.keys())

Index(['main_genre', 'original_title', 'genres', 'poster_url',
       'review_summary', 'agg_rating', 'actors', 'imdb_recommendations',
       'details', 'boxoffice'],
      dtype='object')
Index(['main_genre', 'original_title', 'genres', 'poster_url',
       'review_summary', 'agg_rating', 'actors', 'imdb_recommendations',
       'details', 'boxoffice'],
      dtype='object')
Index(['main_genre', 'original_title', 'genres', 'poster_url',
       'review_summary', 'agg_rating', 'actors', 'imdb_recommendations',
       'details', 'boxoffice'],
      dtype='object')
Index(['main_genre', 'original_title', 'genres', 'poster_url',
       'review_summary', 'agg_rating', 'actors', 'imdb_recommendations',
       'details', 'boxoffice'],
      dtype='object')
Index(['main_genre', 'original_title', 'genres', 'poster_url',
       'review_summary', 'agg_rating', 'actors', 'imdb_recommendations',
       'details', 'boxoffice'],
      dtype='object')
Index(['main_genre', 'original_title', 'genres', '

In [94]:
js = pandas_json.to_dict()

In [96]:
pd.DataFrame(js).to_json('s3://movie-on-friday/metadata/metadata.json',
             storage_options={'key': access_key, 'secret': secret_access_key})

In [154]:
js = pd.read_json('s3://movie-on-friday/metadata/metadata.json', orient='index',
storage_options={'key': access_key, 'secret': secret_access_key})

In [155]:
(~js['genres'].isna()).sum()

18150

In [129]:
js.T['main_genre'].to_dict()

{'/title/tt0002130/': 'Adventure',
 '/title/tt0003740/': 'Adventure',
 '/title/tt0004635/': 'Action',
 '/title/tt0004707/': 'Comedy',
 '/title/tt0004972/': 'Drama',
 '/title/tt0006206/': 'Action',
 '/title/tt0006780/': 'Romance',
 '/title/tt0006864/': 'Drama',
 '/title/tt0009893/': 'Comedy',
 '/title/tt0009900/': 'Adventure',
 '/title/tt0009968/': 'Drama',
 '/title/tt0010323/': 'Horror',
 '/title/tt0010600/': 'Comedy',
 '/title/tt0010726/': 'Adventure',
 '/title/tt0010806/': 'Comedy',
 '/title/tt0011130/': 'Drama',
 '/title/tt0011237/': 'Fantasy',
 '/title/tt0011439/': 'Adventure',
 '/title/tt0011565/': 'Crime',
 '/title/tt0011841/': 'Drama',
 '/title/tt0011870/': 'Drama',
 '/title/tt0012190/': 'Drama',
 '/title/tt0012349/': 'Comedy',
 '/title/tt0012364/': 'Drama',
 '/title/tt0012494/': 'Drama',
 '/title/tt0012532/': 'Drama',
 '/title/tt0012675/': 'Adventure',
 '/title/tt0013086/': 'Crime',
 '/title/tt0013201/': 'Comedy',
 '/title/tt0013442/': 'Fantasy',
 '/title/tt0013556/': 'Adventur

In [108]:
js.T.to_dict()

{'/title/tt0062622/': {'main_genre': 'Adventure'},
 '/title/tt0066921/': {'main_genre': 'Crime'},
 '/title/tt0076759/': {'main_genre': 'Action'},
 '/title/tt0078748/': {'main_genre': 'Horror'},
 '/title/tt0080684/': {'main_genre': 'Action'},
 '/title/tt0083658/': {'main_genre': 'Action'},
 '/title/tt0083866/': {'main_genre': 'Adventure'},
 '/title/tt0084787/': {'main_genre': 'Horror'},
 '/title/tt0086190/': {'main_genre': 'Action'},
 '/title/tt0087332/': {'main_genre': 'Action'},
 '/title/tt0088247/': {'main_genre': 'Action'},
 '/title/tt0088763/': {'main_genre': 'Adventure'},
 '/title/tt0090605/': {'main_genre': 'Action'},
 '/title/tt0093773/': {'main_genre': 'Action'},
 '/title/tt0096874/': {'main_genre': 'Adventure'},
 '/title/tt0099088/': {'main_genre': 'Adventure'},
 '/title/tt0100802/': {'main_genre': 'Action'},
 '/title/tt0103064/': {'main_genre': 'Action'},
 '/title/tt0103644/': {'main_genre': 'Action'},
 '/title/tt0107290/': {'main_genre': 'Action'},
 '/title/tt0114746/': {'ma

In [84]:
import sys

sys.getsizeof(metadata) / 1024 / 1024

1.2500839233398438

In [82]:
len([v for v in metadata.values() if 'original_title' in v])

218

In [80]:
len([v for v in metadata.values() if 'original_title' in v])

118

In [74]:
list(identifiers.MOVIE_COUNT_BY_GENRE.keys())

['action',
 'adventure',
 'animation',
 'biography',
 'comedy',
 'crime',
 'drama',
 'family',
 'fantasy',
 'film-noir',
 'history',
 'horror',
 'music',
 'musical',
 'mystery',
 'romance',
 'sci-fi',
 'sport',
 'thriller',
 'war',
 'western']

In [73]:
pd.read_json('../data/metadata/metadata.json', orient='index')
#.groupby('main_genre').agg({'main_genre': 'count'})

main_genre
/title/tt0002130/  Adventure
/title/tt0003740/  Adventure
/title/tt0004635/     Action
/title/tt0004707/     Comedy
/title/tt0004972/      Drama
...                      ...
/title/tt9898858/     Action
/title/tt9900782/     Action
/title/tt9907782/    Fantasy
/title/tt9911196/     Comedy
/title/tt9916362/      Drama

[23583 rows x 1 columns]

In [66]:
detcol.collect()

Animation              0%|                    | 0/1 [00:00<?, ?it/s]

Horror                 0%|                    | 0/1 [00:01<?, ?it/s]


KeyboardInterrupt: 

'tt0892769'

In [41]:
batman_metadata = detcol.collect_title_details(soup)

In [20]:
batman_metadata.keys()

dict_keys(['original_title', 'genres', 'poster', 'review_summary', 'agg_rating', 'actors', 'imdb_recommendations', 'details', 'boxoffice', 'runtime'])

In [62]:
utils.save_img(p, 'the_dark_knight.jpeg', metadata_config, s3)

SaveResponse(is_successful=True, exception_msg='')

In [141]:
import boto3

# Let's use Amazon S3
s3 = boto3.client('s3', aws_access_key_id=access_key, aws_secret_access_key=secret_access_key)

In [ ]:
s3.

In [145]:
s3.list_objects_v2?

Signature: s3.list_objects_v2(*args, **kwargs)
Docstring:
Returns some or all (up to 1,000) of the objects in a bucket with each request. You can use the request parameters as selection criteria to return a subset of the objects in a bucket. A ``200 OK`` response can contain valid or invalid XML. Make sure to design your application to parse the contents of the response and handle it appropriately. Objects are returned sorted in an ascending order of the respective key names in the list. For more information about listing objects, see `Listing object keys programmatically <https://docs.aws.amazon.com/AmazonS3/latest/userguide/ListingKeysUsingAPIs.html>`__  

 

To use this operation, you must have READ access to the bucket.

 

To use this action in an Identity and Access Management (IAM) policy, you must have permissions to perform the ``s3:ListBucket`` action. The bucket owner has this permission by default and can grant this permission to others. For more information about permissio

In [81]:
dynamodb = boto3.client(
    'dynamodb',
    aws_access_key_id=access_key,
    aws_secret_access_key=secret_access_key,
    region_name=metadata_config['dynamodb_region']
)

In [83]:
dynamodb.list_tables()

{'TableNames': ['movie-metadata'],
 'ResponseMetadata': {'RequestId': 'IDHSVA5468EMB5QEKEAHVNBP2BVV4KQNSO5AEMVJF66Q9ASUAAJG',
  'HTTPStatusCode': 200,
  'HTTPHeaders': {'server': 'Server',
   'date': 'Fri, 03 Jun 2022 17:03:32 GMT',
   'content-type': 'application/x-amz-json-1.0',
   'content-length': '33',
   'connection': 'keep-alive',
   'x-amzn-requestid': 'IDHSVA5468EMB5QEKEAHVNBP2BVV4KQNSO5AEMVJF66Q9ASUAAJG',
   'x-amz-crc32': '3100087865'},
  'RetryAttempts': 0}}

In [65]:
dir_path = os.path.join('..', 'data', 'metadata')
dfs = []
for f in os.listdir(dir_path):
    if '.csv' not in f:
        continue
    file_path = os.path.join(dir_path, f)
    dfs.append(pd.read_csv(file_path))

ids = pd.concat(dfs)
ids.head()

title_id main_genre
0  /title/tt0468569/      crime
1  /title/tt0110912/      crime
2  /title/tt0068646/      crime
3  /title/tt1345836/      crime
4  /title/tt0114369/      crime

In [91]:
metadata_path = '../data/metadata/metadata.json'
ids.setto_json(metadata_path, orient='split')

In [97]:
URL_TEMPLATE = (
    'https://www.imdb.com/search/title/?title_type=feature&genres={}'
    '&sort=num_votes,desc&start={}&explore=genres&ref_=adv_nxt'
)
url = URL_TEMPLATE.format('action', 1)
url

'https://www.imdb.com/search/title/?title_type=feature&genres=action&sort=num_votes,desc&start=1&explore=genres&ref_=adv_nxt'

In [98]:
response = requests.get(url, headers={"Accept-Language": "en-US,en;q=0.5"})
ranking_soup = bs.BeautifulSoup(response.text, 'lxml')

In [144]:
j = {
    '/title/tt0468569/': {
        'main_genre': 'Action',
        'runtime': '2h'
    },
    '/title/tt1375666/': {
        'main_genre': 'Action',
        'runtime': '2h'
    }
}
j

{'/title/tt0468569/': {'main_genre': 'Action', 'runtime': '2h'},
 '/title/tt1375666/': {'main_genre': 'Action', 'runtime': '2h'}}

In [146]:
pd.DataFrame(j).T.to_json(metadata_path)

In [157]:
utils.write_json(j, metadata_path)

In [170]:
metadata_id = utils.read_json(metadata_path)
len(metadata_id)

3513

In [148]:
import pandas as pd
from recsys.core.data import CSVDataLoader
from recsys.etl.transformers import RawReviewsTransformer, RawDetailsTransformer
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [149]:
data_path = '../data/raw/details/1pct/action.csv'
loader = CSVDataLoader(data_path)
action_proc = RawDetailsTransformer(loader).transform()

In [150]:
action = loader.load_data()
action.head()

original_title  \
0                    Original title: The Dark Knight   
1                          Original title: Inception   
2                         Original title: The Matrix   
3  Original title: The Lord of the Rings: The Fel...   
4  Original title: The Lord of the Rings: The Ret...   

                                      review_summary  agg_rating  \
0  {'n_user_reviews': '7.7KUser reviews', 'n_crit...  9.0/102.5M   
1  {'n_user_reviews': '4.4KUser reviews', 'n_crit...  8.8/102.2M   
2  {'n_user_reviews': '4.6KUser reviews', 'n_crit...  8.7/101.8M   
3  {'n_user_reviews': '5.5KUser reviews', 'n_crit...  8.8/101.7M   
4  {'n_user_reviews': '3.9KUser reviews', 'n_crit...  8.9/101.7M   

                                              actors  \
0  {'Christian Bale': '/name/nm0000288?ref_=tt_cl...   
1  {'Leonardo DiCaprio': '/name/nm0000138?ref_=tt...   
2  {'Keanu Reeves': '/name/nm0000206?ref_=tt_cl_t...   
3  {'Elijah Wood': '/name/nm0000704?ref_=tt_cl_t_...   
4  {'Elijah Wood': '/name/nm0000704?ref_=tt_cl_t_...   

                                imdb_recommendations  \
0  ['/title/tt1345836/?ref_=tt_sims_tt_t_1', '/ti...   
1  ['/title/tt0816692/?ref_=tt_sims_tt_t_1', '/ti...   
2  ['/title/tt1375666/?ref_=tt_sims_tt_t_1', '/ti...   
3  ['/title/tt0167261/?ref_=tt_sims_tt_t_1', '/ti...   
4  ['/title/tt0167261/?ref_=tt_sims_tt_t_1', '/ti...   

                                           storyline  \
0  Set within a year after the events of Batman B...   
1  Dom Cobb is a skilled thief, the absolute best...   
2  Thomas A. Anderson is a man living two lives. ...   
3  An ancient Ring thought lost for centuries has...   
4  The final confrontation between the forces of ...   

                                       tagline     certificate  \
0                      TaglinesWhy So Serious?  Certificate14+   
1  TaglinesYour mind is the scene of the crime  Certificate12+   
2                       TaglinesFree your mind  Certificate16+   
3             TaglinesThe Legend Comes to Life  Certificate12+   
4      TaglinesThe eye of the enemy is moving.  Certificate12+   

                                             details  \
0  Release dateAugust 14, 2008 (Russia)Countries ...   
1  Release dateJuly 22, 2010 (Russia)Countries of...   
2  Release dateOctober 14, 1999 (Russia)Countries...   
3  Release dateMarch 1, 2002 (Russia)Countries of...   
4  Release dateJanuary 22, 2004 (Russia)Countries...   

                                           boxoffice  \
0  Budget$185,000,000 (estimated)Gross US & Canad...   
1  Budget$160,000,000 (estimated)Gross US & Canad...   
2  Budget$63,000,000 (estimated)Gross US & Canada...   
3  Budget$93,000,000 (estimated)Gross US & Canada...   
4  Budget$94,000,000 (estimated)Gross US & Canada...   

                                           techspecs           title_id  
0  Runtime2 hours 32 minutesSound mixDolby Digita...  /title/tt0468569/  
1  Runtime2 hours 28 minutesColorColorSound mixDo...  /title/tt1375666/  
2  Runtime2 hours 16 minutesColorColorSound mixDo...  /title/tt0133093/  
3  Runtime2 hours 58 minutesColorColorSound mixDT...  /title/tt0120737/  
4  Runtime3 hours 21 minutesColorColorSound mixDT...  /title/tt0167260/

In [151]:
from recsys.etl.functions import extract_movie_details

In [154]:
extract_movie_details(action.iloc[:2,:])

original_title  \
0  Original title: The Dark Knight   
1        Original title: Inception   

                                      review_summary  agg_rating  \
0  {'n_user_reviews': '7.7KUser reviews', 'n_crit...  9.0/102.5M   
1  {'n_user_reviews': '4.4KUser reviews', 'n_crit...  8.8/102.2M   

                                              actors  \
0  {'Christian Bale': '/name/nm0000288?ref_=tt_cl...   
1  {'Leonardo DiCaprio': '/name/nm0000138?ref_=tt...   

                                imdb_recommendations  \
0  ['/title/tt1345836/?ref_=tt_sims_tt_t_1', '/ti...   
1  ['/title/tt0816692/?ref_=tt_sims_tt_t_1', '/ti...   

                                           storyline  \
0  Set within a year after the events of Batman B...   
1  Dom Cobb is a skilled thief, the absolute best...   

                                       tagline     certificate  \
0                      TaglinesWhy So Serious?  Certificate14+   
1  TaglinesYour mind is the scene of the crime  Certificate12+   

                                           boxoffice  \
0  Budget$185,000,000 (estimated)Gross US & Canad...   
1  Budget$160,000,000 (estimated)Gross US & Canad...   

                                           techspecs           title_id  \
0  Runtime2 hours 32 minutesSound mixDolby Digita...  /title/tt0468569/   
1  Runtime2 hours 28 minutesColorColorSound mixDo...  /title/tt1375666/   

  release_date                country_of_origin  \
0   2008-08-14  [United States, United Kingdom]   
1   2010-07-22  [United Kingdom, United States]   

                                 production_company  
0  [Warner Bros., Legendary Entertainment, Syncopy]  
1  [Warner Bros., Legendary Entertainment, Syncopy]

In [8]:
data_path = '../data/raw/reviews/1pct/action.csv'
loader = CSVDataLoader(data_path)

In [10]:
action = loader.load_data()
action.head()

id                                               text  \
0  /title/tt0468569/  Best movie ever. Heath ledger's work is phenom...   
1  /title/tt0468569/  Totally one of the greatest movie titles ever ...   
2  /title/tt0468569/  This movie is a work of art. The finest sequel...   
3  /title/tt0468569/  Confidently directed, dark, brooding, and pack...   
4  /title/tt0468569/  It is just what you want for the best movie. G...   

   rating              date  \
0    10.0   12 January 2021   
1    10.0    9 January 2021   
2    10.0  17 February 2021   
3    10.0  12 February 2020   
4    10.0    7 October 2019   

                                               title  \
0                                    Perfect combo\n   
1                                  The Dark Knight\n   
2   This town deserves a better class of criminal!\n   
3                                  The Dark Knight\n   
4                                      MASTERPIECE\n   

                           author  \
0   /user/ur95396995/?ref_=tt_urv   
1  /user/ur109215140/?ref_=tt_urv   
2  /user/ur129557514/?ref_=tt_urv   
3   /user/ur87850731/?ref_=tt_urv   
4  /user/ur108519953/?ref_=tt_urv   

                                         helpfulness  
0  \n                    171 out of 185 found thi...  
1  \n                    144 out of 158 found thi...  
2  \n                    50 out of 54 found this ...  
3  \n                    404 out of 471 found thi...  
4  \n                    217 out of 251 found thi...

In [27]:
action['text'][15]

'If someone else acted as Joker, I would give the movie 7-8 stars. The majority of people ended up loving the villain more than the hero, and that rarely happends in movies.Rest in peace Heath Ledger.'

In [28]:
reviews_processor = RawReviewsTransformer(loader)
a = reviews_processor.transform()

In [33]:
a['author'].str.split('?', expand=True)[0]

0         /user/ur95396995/
1        /user/ur109215140/
2        /user/ur129557514/
3         /user/ur87850731/
4        /user/ur108519953/
                ...        
66269     /user/ur53639379/
66270     /user/ur51801975/
66271     /user/ur36303263/
66272     /user/ur35145579/
66273     /user/ur44754847/
Name: 0, Length: 66274, dtype: object

In [36]:
a['title'].str.split('\n', expand=True)[0]

0                                          Perfect combo
1                                        The Dark Knight
2         This town deserves a better class of criminal!
3                                        The Dark Knight
4                                            MASTERPIECE
                              ...                       
66269                                 Unbelievably awful
66270                          How is this rated so low?
66271                     Good film despite bad reviews.
66272                 Pretty funny for a buddy cop movie
66273                                        Funny movie
Name: 0, Length: 66274, dtype: object